In [1]:
import pandas as pd
import gradio as gr
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt
import seaborn as sns

/Users/cyberosa/.pyenv/versions/hf_dashboards/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
div_data = pd.read_parquet("../data/closed_markets_div.parquet")

In [3]:
div_data.loc[div_data["off_by_perc"]>=90]

currentAnswer                                          id  \
315            no  0x29462bf8c8f24772cd6da03878a4aee5c5813474   
323           yes  0x0ad9d4edb0a401ec9a5b4f2ccf7942d28c29d4e3   

    openingTimestamp market_creator    opening_datetime  first_outcome_prob  \
315       1724976000          pearl 2024-08-30 02:00:00              0.9416   
323       1724976000     quickstart 2024-08-30 02:00:00              0.0499   

     second_outcome_prob  kl_divergence  off_by_perc  
315               0.0584       2.840439        94.16  
323               0.9501       2.997734        95.01

In [5]:
div_data.loc[div_data["kl_divergence"]>=2.0]

currentAnswer                                          id  \
52             no  0x927beda324bfd4514a7b64ab5594451fdaf4796e   
293           yes  0x90bb15982f2b5a5f044ad8ff49fe20daddfb8ca7   
315            no  0x29462bf8c8f24772cd6da03878a4aee5c5813474   
323           yes  0x0ad9d4edb0a401ec9a5b4f2ccf7942d28c29d4e3   

    openingTimestamp market_creator    opening_datetime  first_outcome_prob  \
52        1722816000     quickstart 2024-08-05 02:00:00              0.8792   
293       1724803200     quickstart 2024-08-28 02:00:00              0.1166   
315       1724976000          pearl 2024-08-30 02:00:00              0.9416   
323       1724976000     quickstart 2024-08-30 02:00:00              0.0499   

     second_outcome_prob  kl_divergence  off_by_perc  
52                0.1208       2.113619        87.92  
293               0.8834       2.149006        88.34  
315               0.0584       2.840439        94.16  
323               0.9501       2.997734        95.01

In [ ]:
all_markets = closed_markets.copy(deep=True)
    all_markets["market_creator"] = "all"

    # merging both dataframes
    final_markets = pd.concat([div_data, all_markets], ignore_index=True)
    final_markets = final_markets.sort_values(by="opening_datetime", ascending=True)

    # Create the main figure and axis
    fig, ax1 = plt.subplots(figsize=(10, 6))

    # Create the boxplot using seaborn
    sns.boxplot(
        data=closed_markets,
        x="month_year_week",
        y="kl_divergence",
        ax=ax1,
        hue="market_creator",
        order=["pearl", "quickstart", "all"],
    )

    # Set labels and title for the main axis
    ax1.set_xlabel("Week")
    ax1.set_ylabel("KL Divergence")
    ax1.set_title("KL Divergence Boxplot with Off-by Percentage")

    # Create a secondary y-axis
    ax2 = ax1.twinx()

    # Plot the off_by_perc values on the secondary y-axis
    for i, week in enumerate(closed_markets["month_year_week"].unique()):
        off_by_perc = closed_markets[closed_markets["month_year_week"] == week][
            "off_by_perc"
        ]
        ax2.scatter([i] * len(off_by_perc), off_by_perc, color="red", alpha=0.01)

    # Set label for the secondary y-axis
    ax2.set_ylabel("Off-by Percentage")

    # Adjust the layout and display the plot
    plt.tight_layout()